<div style="text-align: center">
  <img alt="AIcrowd" src="https://i.imgur.com/sw8hRwM.jpg">
</div>

# How to use this notebook 📝

1. **Copy the notebook**. This is a shared template and any edits you make here will not be saved. _You should copy it into your own drive folder._ For this, click the "File" menu (top-left), then "Save a Copy in Drive". You can edit your copy however you like.
2. **Link it to your AIcrowd account**. In order to submit your code to AIcrowd, you need to add ssh key to your GitLab account temporarily.
3. **Stick to the classes definitions**. The submission to AIcrowd will look for the pre-defined class names.

# Your music demixing solution 🚀 

In this notebook, you can play with the data, and define and train your music demixing model. You can then directly submit it to the AIcrowd, with some magic code at the end.

### Baselines
You can also play with the baselines available in example below!

# Setup the notebook 🛠

In [ ]:
!pip install -q -U "tqdm<4.60"
!apt install git-lfs
!git clone https://github.com/AIcrowd/music-demixing-challenge-starter-kit.git > /dev/null
%cd music-demixing-challenge-starter-kit
!git lfs pull

     |████████████████████████████████| 81kB 7.1MB/s 
Reading package lists... Done
Building dependency tree       
Reading state information... Done
The following package was automatically installed and is no longer required:
  libnvidia-common-460
Use 'apt autoremove' to remove it.
The following NEW packages will be installed:
  git-lfs
0 upgraded, 1 newly installed, 0 to remove and 34 not upgraded.
Need to get 2,129 kB of archives.
After this operation, 7,662 kB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu bionic/universe amd64 git-lfs amd64 2.3.4-1 [2,129 kB]
Fetched 2,129 kB in 1s (2,909 kB/s)
Selecting previously unselected package git-lfs.
(Reading database ... 160706 files and directories currently installed.)
Preparing to unpack .../git-lfs_2.3.4-1_amd64.deb ...
Unpacking git-lfs (2.3.4-1) ...
Setting up git-lfs (2.3.4-1) ...
Processing triggers for man-db (2.8.3-2ubuntu0.1) ...
Cloning into 'music-demixing-challenge-starter-kit'...
remote: Enu

### 👇 Run the below collapsed cell for helper functions

In [ ]:
#@title
import os
import IPython
import pprint

def display_result(path):
  print(path)
  print("🔈 Bass:")
  display(IPython.display.Audio(path + "/bass.wav"))
  print("🥁 Drums:")
  display(IPython.display.Audio(path + "/drums.wav"))
  print("🎹 Other:")
  display(IPython.display.Audio(path + "/other.wav"))
  print("🎤 Vocals:")
  display(IPython.display.Audio(path + "/vocals.wav"))

def install_pip_and_apt_on_colab():
  default_requirements = open("requirements.txt").read().split('\n')
  local_pip_install = " ".join(default_requirements + PIP_PACKAGES)
  default_packages = open("apt.txt").read().split('\n')
  local_apt_install = " ".join(default_packages + APT_PACKAGES)
  !pip install -q $local_pip_install
  !apt install -y {local_apt_install}

def write_custom_implementation(file_name):
  relevant_cell = None
  for i in _ih[::-1]:
    if "bfb41056a0e55e7b715c21ea9285cb1c" in i and "relevant_cell" not in i:
      relevant_cell = i

  if relevant_cell is None:
    raise Exception("Did you run your custom code?")

  with open(file_name, "w") as f:
    f.write(relevant_cell)

def add_models_to_submission(model_regex):
  import os
  echo_and_run("git lfs install")
  echo_and_run("git lfs track \"%s\"" % model_regex)
  echo_and_run("git add .gitattributes")

def echo_and_run(command):
  print("#> " + command)
  return os.system(command)

def make_submission():
  status_code = echo_and_run("ssh -o StrictHostKeyChecking=no -T git@gitlab.aicrowd.com")
  if status_code > 1:
    raise Exception("SSH login failed, did you add above SSH key in your account?")
  !git push aicrowd master -f
  !git push aicrowd --tags

def prepare_for_submission(class_name, commit_message=None):
  import datetime
  import time
  timestamp_now = int(time.time())
  time_now = datetime.datetime.utcnow().strftime('%B %d %Y - %H:%M:%S')
  file_name = os.popen("grep -nr \"class %s\" *.py" % class_name).read().split(':')[0].split('.')[0]
  predict_py_content = """#!/usr/bin/env python
from {file_name} import {class_name}

submission = {class_name}()
submission.run()
print("Successfully completed music demixing...")
""".format(class_name=class_name, file_name=file_name)
  with open("predict.py", "w") as f:
    f.write(predict_py_content)

  echo_and_run("git add .")
  if not commit_message:
    commit_message = "Automated submission via notebook: %s" % time_now
  if not AICROWD_USER_NAME or not AICROWD_EMAIL_ID:
    raise Exception("AICROWD_USER_NAME or AICROWD_EMAIL_ID not configured")
  echo_and_run("git config --global user.name \"%s\"" % AICROWD_USER_NAME)
  echo_and_run("git config --global user.email \"%s\"" % AICROWD_EMAIL_ID)
  echo_and_run("git commit -m \"%s\"" % commit_message)
  echo_and_run("git remote add aicrowd git@gitlab.aicrowd.com:%s/music-demixing-challenge-starter-kit.git" % AICROWD_USER_NAME)
  echo_and_run("git tag submission-v%s" % timestamp_now)
  if not os.path.isfile("/root/.ssh/id_rsa.pub"):
    echo_and_run('cat /dev/zero | ssh-keygen -q -N "" > /dev/null')
  ssh_pub = open("/root/.ssh/id_rsa.pub").read()
  return IPython.display.HTML("""
  <h3>👉 Copy paste below ssh key to your profile: 
    <a href="https://gitlab.aicrowd.com/profile/keys" target="_blank">Add</a>
  </h3>
  <i>Please remove the SSH key from your profile after you make your submission.<i>
  <br>
  <textarea cols=100 rows=10>%s</textarea>""" % ssh_pub)

# Configure your environment 📎
<a name="static-var"></a>

In [ ]:
# Additional **pip** packages required by your submission
# Default list: https://github.com/AIcrowd/music-demixing-challenge-starter-kit/blob/master/requirements.txt
PIP_PACKAGES = [
    'musdb',
]

# Additional **apt** packages required by your submission.
# Default list: https://github.com/AIcrowd/music-demixing-challenge-starter-kit/blob/master/apt.txt
APT_PACKAGES = [
    'ffmpeg',
]

install_pip_and_apt_on_colab()

ERROR: botocore 1.20.72 has requirement urllib3<1.27,>=1.25.4, but you'll have urllib3 1.24.3 which is incompatible.
Reading package lists... Done
Building dependency tree       
Reading state information... Done
build-essential is already the newest version (12.4ubuntu1).
git is already the newest version (1:2.17.1-1ubuntu0.8).
libsndfile1 is already the newest version (1.0.28-4ubuntu0.18.04.1).
ffmpeg is already the newest version (7:3.4.8-0ubuntu0.2).
The following package was automatically installed and is no longer required:
  libnvidia-common-460
Use 'apt autoremove' to remove it.
The following additional packages will be installed:
  libao-common libao4 libid3tag0 libmad0 libmagic-mgc libmagic1
  libopencore-amrnb0 libopencore-amrwb0 libsox-fmt-alsa libsox-fmt-ao
  libsox-fmt-base libsox-fmt-mp3 libsox-fmt-oss libsox-fmt-pulse libsox3
Suggested packages:
  libaudio2 file
The following NEW packages will be installed:
  libao-common libao4 libid3tag0 libmad0 libmagic-mgc libmagic1

# Download dataset files 💾

In [ ]:
# You can select to download full dataset or 7s dataset, it will be present in `data/` folder.
# !python utility/verify_or_download_data.py

# Baselines 🗃

Let's go through few of the baselines, before jumping to the problem! 



🎶 Let's listen to example song added as part of starter kit.

In [ ]:
import IPython, os

print("Original mixture:")
IPython.display.Audio("data/test/Mu - Too Bright/mixture.wav")

Original mixture:


## XUMXPredictor
This uses CrossNet-UMX (X-UMX) for music demixing.

In [ ]:
!mkdir models && cd models && wget https://zenodo.org/record/4740378/files/pretrained_xumx_musdb18HQ.pth

from test_xumx import XUMXPredictor
xumx_predictor = XUMXPredictor()
xumx_predictor.evaluation()
xumx_predictor.scoring()

--2021-05-12 22:03:02--  https://zenodo.org/record/4740378/files/pretrained_xumx_musdb18HQ.pth
Resolving zenodo.org (zenodo.org)... 137.138.76.77
Connecting to zenodo.org (zenodo.org)|137.138.76.77|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 142537840 (136M) [application/octet-stream]
Saving to: ‘pretrained_xumx_musdb18HQ.pth’

pretrained_xumx_mus 100%[===================>] 135.93M  10.3MB/s    in 11s     

2021-05-12 22:03:13 (12.9 MB/s) - ‘pretrained_xumx_musdb18HQ.pth’ saved [142537840/142537840]

Evaluating for: Mu - Too Bright


{'Mu - Too Bright': {'sdr': 9.082310676574707,
  'sdr_bass': 4.60244083404541,
  'sdr_drums': 13.450826644897461,
  'sdr_other': 5.252285957336426,
  'sdr_vocals': 13.023689270019531}}

In [ ]:
display_result("data/results/Mu - Too Bright")

Output hidden; open in https://colab.research.google.com to view.

## openunmix
This uses openunmix for music demixing.

In [ ]:
from test_umx import UMXPredictor
umx_predictor = UMXPredictor()
umx_predictor.evaluation()
umx_predictor.scoring()

Downloading: "https://github.com/sigsep/open-unmix-pytorch/archive/master.zip" to ./models/master.zip
Downloading: "https://zenodo.org/api/files/1c8f83c5-33a5-4f59-b109-721fdd234875/vocals-b62c91ce.pth" to ./models/checkpoints/vocals-b62c91ce.pth


  0%|          | 0.00/34.0M [00:00<?, ?B/s]

Downloading: "https://zenodo.org/api/files/1c8f83c5-33a5-4f59-b109-721fdd234875/drums-9619578f.pth" to ./models/checkpoints/drums-9619578f.pth


  0%|          | 0.00/34.0M [00:00<?, ?B/s]

Downloading: "https://zenodo.org/api/files/1c8f83c5-33a5-4f59-b109-721fdd234875/bass-8d85a5bd.pth" to ./models/checkpoints/bass-8d85a5bd.pth


  0%|          | 0.00/34.0M [00:00<?, ?B/s]

Downloading: "https://zenodo.org/api/files/1c8f83c5-33a5-4f59-b109-721fdd234875/other-b52fbbf7.pth" to ./models/checkpoints/other-b52fbbf7.pth


  0%|          | 0.00/34.0M [00:00<?, ?B/s]

/content/music-demixing-challenge-starter-kit/data/test/Mu - Too Bright/mixture.wav: prediction completed.
Evaluating for: Mu - Too Bright


{'Mu - Too Bright': {'sdr': 9.23303508758545,
  'sdr_bass': 4.832416534423828,
  'sdr_drums': 13.429330825805664,
  'sdr_other': 5.699060440063477,
  'sdr_vocals': 12.971332550048828}}

In [ ]:
display_result("data/results/Mu - Too Bright")

Output hidden; open in https://colab.research.google.com to view.

## Your implementation here!! 🎉 

You can write your own implementation in this cell OR use any of available baseline.

In [ ]:
# Your training code

In [ ]:
#!/usr/bin/env python
# This file is the entrypoint for your submission.
# You can modify this file to include your code or directly call your functions/modules from here.
#### Magic bfb41056a0e55e7b715c21ea9285cb1c: Do not remove it, it is used to detect your code in notebook.

import shutil
import soundfile as sf
from evaluator.music_demixing import MusicDemixingPredictor


class CustomPredictor(MusicDemixingPredictor):

    def prediction_setup(self):
        # Load your model here.
        # self.separator = torch.hub.load('sigsep/open-unmix-pytorch', 'umxhq')
        pass

    """
    PARTICIPANT_TODO:
    During the evaluation all music files will be provided one by one, along with destination path
    for saving separated audios.

    NOTE: In case you want to load your model, please do so in `predict_setup` function.
    """
    def prediction(self, mixture_file_path, bass_file_path, drums_file_path, other_file_path, vocals_file_path):
        # Write your prediction code here:
        # [...]
        # estimates = separator(audio)
        # Save the wav files at assigned locations.

        print("Mixture file is present at following location: %s" % mixture_file_path)
        x, rate = sf.read(mixture_file_path)  # mixture is stereo with sample rate of 44.1kHz
        n_sources = 4
        sf.write(bass_file_path, 1/n_sources * x, rate)
        sf.write(drums_file_path, 1/n_sources * x, rate)
        sf.write(other_file_path, 1/n_sources * x, rate)
        sf.write(vocals_file_path, 1/n_sources * x, rate)
        print("%s: prediction completed." % mixture_file_path)


if __name__ == "__main__":
  submission = CustomPredictor()
  submission.evaluation()
  pprint.pprint(submission.scoring())

Mixture file is present at following location: /content/music-demixing-challenge-starter-kit/data/test/Mu - Too Bright/mixture.wav
/content/music-demixing-challenge-starter-kit/data/test/Mu - Too Bright/mixture.wav: prediction completed.
Evaluating for: Mu - Too Bright
{'Mu - Too Bright': {'sdr': 0.6527892760932446,
                     'sdr_bass': -1.0531526803970337,
                     'sdr_drums': 2.036451816558838,
                     'sdr_other': 0.11387090384960175,
                     'sdr_vocals': 1.5139870643615723}}


In [ ]:
display_result("data/results/Mu - Too Bright")

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
# ENABLE BELOW FUNCTIONS IF YOU ARE DOING CUSTOM IMPLEMENTATION
#
write_custom_implementation("test.py")
add_models_to_submission("*.pt") #<- extension of files work, will be added via git-lfs

#> git lfs install
#> git lfs track "*.pt"
#> git add .gitattributes


# Ready? Submit to AIcrowd 🚀

If you are satisfied with your code, run the code below to send your code to the AIcrowd servers for evaluation! 

**Make sure you have included all packages needed to run your code in the [_"Packages"_](#packages) section.**

In [ ]:
!git tag -d $(git tag -l)

AICROWD_USER_NAME = 'shivam'
AICROWD_EMAIL_ID = 'shivam@aicrowd.com' # used for commit email, can be anything of your wish
# SUBMISSION_CLASS = "UMXPredictor"
# SUBMISSION_CLASS = "XUMXPredictor"
SUBMISSION_CLASS = "CustomPredictor"

prepare_for_submission(SUBMISSION_CLASS, commit_message="Meaningful description to my submission")

#> git add .
#> git config --global user.name "shivam"
#> git config --global user.email "shivam@aicrowd.com"
#> git commit -m "Automated submission via notebook: May 12 2021 - 22:03:53"
#> git remote add aicrowd git@gitlab.aicrowd.com:shivam/music-demixing-challenge-starter-kit.git
#> git tag submission-v1620857033
#> cat /dev/zero | ssh-keygen -q -N "" > /dev/null


In [ ]:
make_submission()

#> ssh -o StrictHostKeyChecking=no -T git@gitlab.aicrowd.com
Locking support detected on remote "aicrowd". Consider enabling it with:
  $ git config lfs.https://gitlab.aicrowd.com/shivam/music-demixing-challenge-starter-kit.git/info/lfs.locksverify true
Git LFS: (5 of 5 files, 5 skipped) 271.88 MB / 271.88 MB, 5.89 MB skipped
Counting objects: 249, done.
Delta compression using up to 2 threads.
Compressing objects: 100% (156/156), done.
Writing objects: 100% (249/249), 5.21 MiB | 6.72 MiB/s, done.
Total 249 (delta 91), reused 168 (delta 82)
remote: Resolving deltas: 100% (91/91), done.
To gitlab.aicrowd.com:shivam/music-demixing-challenge-starter-kit.git
 + ad565d4...d4d0db1 master -> master (forced update)
Locking support detected on remote "aicrowd". Consider enabling it with:
  $ git config lfs.https://gitlab.aicrowd.com/shivam/music-demixing-challenge-starter-kit.git/info/lfs.locksverify true
Total 0 (delta 0), reused 0 (delta 0)
remote: 
remote:           #///(            )///#
re